+++
notebook = true
title = "Creating OpenGeoSys Mesh with Inclined Borehole Heat Exchangers"
date = "2023-11-27"
author = "Joy Brato Shil, Haibing Shao"
image = "inclined2DBHE.png"
+++


<div class="note">
    <p style="margin-top: 0; margin-bottom: 0;">
        <img style="margin-top: 0; margin-bottom: 0; height: 2em;" class="inline-block mr-2 no-fancybox"
            src="https://upload.wikimedia.org/wikipedia/commons/3/38/Jupyter_logo.svg" alt="">
        This page is based on a Jupyter notebook.
<a href="./inclined_bhe_meshing.ipynb" download="inclined_bhe_meshing.ipynb"><img class="no-fancybox" style="display: inline; margin-top: 0; margin-bottom: 0; margin-left: 1em;" src="https://img.shields.io/static/v1?label=Download:&message=inclined_bhe_meshing.ipynb&color=blue" /></a>
<a href="https://gitlab.opengeosys.org/ogs/ogs/-/blob/master/Tests/Data/../../web/content/docs/tutorials/Inclined_bhe_meshing/notebook-inclined_bhe_meshing.md"><img src="https://img.shields.io/static/v1?label=Source:&message=notebook-inclined_bhe_meshing.md&color=brightgreen" class="no-fancybox"
        style="display: inline; margin-top: 0; margin-bottom: 0; margin-left: 1em;" /></a>
<a href="https://binder.opengeosys.org/v2/gh/bilke/binder-ogs-requirements/6.5.6-0.7.0?urlpath=git-pull%3Frepo=https://gitlab.opengeosys.org/ogs/ogs%26urlpath=lab/tree/ogs/Tests/Data/../../web/content/docs/tutorials/Inclined_bhe_meshing/notebook-inclined_bhe_meshing.md%26branch=6.5.6%26depth=1">
    <img class="no-fancybox" style="display: inline; margin-top: 0; margin-bottom: 0; margin-left: 1em;"
        src="https://img.shields.io/static/v1?label=&message=Launch notebook&color=5c5c5c&logo=" />
</a></p></div>

This tutorial is made to illustrate the procedure of creating an OGS mesh file with inclined Borehole Heat Exchangers (BHEs) in it. Such mesh uses prism, tetrahedron and pyramid elements for the soil part, and line elements for the BHEs. In this tutorial of inclined BHEs, a layer of hexagonal shape prism elements are created around each BHE for optimal accuracy (Diersch et al. 2011) and all other parts of the geometry consist of tetrahedron and pyramid elements. The produced mesh file is made explicitly for the HEAT_TRANSPORT_BHE module in OGS and will NOT work with other modules. For better understanding, an image of 1D inclined BHEs is presented.

![inclined_bhe_1D.png](./inclined_bhe_1D.png)

First, external packages have  been imported and Gmsh is initialized.

In [1]:
import os
import sys
from pathlib import Path

import gmsh

gmsh.initialize()

The geometry is a 3D structure that has 3 boreholes (2 inclined and 1 vertical) in it. Similar to the previous tutorial of BHEs, the first step is to create the surface 1 with all the necessary points which regulate the borehole locations, as well as the mesh size. Now, we define the basic geometry of the BHEs, as well as the element sizes around them.

In [2]:
# environment variable for output path
out_dir = Path(os.environ.get("OGS_TESTRUNNER_OUT_DIR", "_out"))
out_dir.mkdir(parents=True, exist_ok=True)

exe_dir = os.environ.get("OGS_BINARY_DIR")

# mesh file name
bhe_mesh_file_name = "inclined_bhe_mesh_file"

# geometry parameters
width = 20
length = 20
depth = 12
bhe_depth = depth - 2

# element sizes
bhe_radius = 0.07
alpha = 6.134  # see Diersch et al. 2011 Part 2
delta = (
    alpha * bhe_radius
)  # meshsize at BHE and distance of the surrounding optimal mesh points
elem_size = 0.5

In this step, we are going to create the top surface using the python interface of Gmsh.
To create a point with the built-in CAD kernel, the Python API function `gmsh.model.geo.addPoint()` is used.
The first 3 arguments are the point coordinates (x, y, z).
The next (optional) argument is the target mesh size close to the point.
The last (optional) argument is the point tag (a strictly positive integer that uniquely identifies the point).
Here, we have assigned 4 boundary points.

In [3]:
# cube surface
gmsh.model.geo.addPoint(-width / 2.0, 0.0, 0.0, elem_size, 1)
gmsh.model.geo.addPoint(width / 2.0, 0.0, 0.0, elem_size, 2)
gmsh.model.geo.addPoint(width / 2.0, length, 0.0, elem_size, 3)
gmsh.model.geo.addPoint(-width / 2.0, length, 0.0, elem_size, 4)

4

Next, the API function `gmsh.model.geo.addLine` is used to create straight-line segments with the built-in kernel follows the same conventions:
the first 2 arguments are point tags (the start and end points of the line), and the last (optional) is the line tag. Note that curve tags are separate from point tags.
Hence we can reuse tag '1' for our first curve. And as a general rule, elementary entity tags in Gmsh have to be unique per geometrical dimension.

In [4]:
gmsh.model.geo.addLine(1, 2, 1)
gmsh.model.geo.addLine(2, 3, 2)
gmsh.model.geo.addLine(3, 4, 3)
gmsh.model.geo.addLine(4, 1, 4)

4

Next, a curve loop has been defined by using the ordered list of 4 connected lines.
The API function to create curve loops takes a list of integers as the first argument, and the curve loop tag (which must be unique amongst curve loops) as the second (optional) argument.

In [5]:
gmsh.model.geo.addCurveLoop([1, 2, 3, 4], 1)

1

In this step, the structure of the geometry is added.
In order to create the structure, bottom surface and other surrounding surfaces have been created using similar method to the top surface.
Hence, four points of the bottom surface have been added.
Later, all necessary lines have been added to build the 3D geometry.
Next, 5 curve loops (4 surroundings and 1 bottom) have been defined and corresponding plane surface is added using the API function `gmsh.model.geo.addPlaneSurface`.

In [6]:
gmsh.model.geo.addPoint(-width / 2.0, 0.0, -depth, elem_size, 101)
gmsh.model.geo.addPoint(width / 2.0, 0.0, -depth, elem_size, 102)
gmsh.model.geo.addPoint(width / 2.0, length, -depth, elem_size, 103)
gmsh.model.geo.addPoint(-width / 2.0, length, -depth, elem_size, 104)

gmsh.model.geo.addLine(1, 101, 101)
gmsh.model.geo.addLine(2, 102, 102)
gmsh.model.geo.addLine(3, 103, 103)
gmsh.model.geo.addLine(4, 104, 104)
gmsh.model.geo.addLine(101, 102, 105)
gmsh.model.geo.addLine(102, 103, 106)
gmsh.model.geo.addLine(103, 104, 107)
gmsh.model.geo.addLine(104, 101, 108)


gmsh.model.geo.addCurveLoop([105, 106, 107, 108], 5)
gmsh.model.geo.addCurveLoop([2, 103, -106, -102], 6)
gmsh.model.geo.addCurveLoop([3, 104, -107, -103], 7)
gmsh.model.geo.addCurveLoop([4, 101, -108, -104], 8)
gmsh.model.geo.addCurveLoop([1, 102, -105, -101], 9)

gmsh.model.geo.addPlaneSurface([5], 5)
gmsh.model.geo.addPlaneSurface([6], 6)
gmsh.model.geo.addPlaneSurface([7], 7)
gmsh.model.geo.addPlaneSurface([8], 8)
gmsh.model.geo.addPlaneSurface([9], 9)

9

Now, 3 BHE surfaces have been created using parameters such as BHE coordinates, delta. The BHE node is surrounded by the 6 additional nodes in hexagonal shape which will create better mesh for optimal accuracy (Diersch et al. 2011 Part 2 DOI:10.1016/j.cageo.2010.08.002).

![Inclined_bhe_top_view.png](./Inclined_bhe_top_view.png)

For each BHE node, 6 additional nodes and 6 corresponding line are added.
After that, a curve loop is created using 6 lines.
Then, the BHE surface is defined using that curve loop.
Following the same method, BHE surface 2 and 3 have been created.

In [7]:
# BHE surfaces 1
gmsh.model.geo.addPoint(-6, 10, 0, delta, 5)
gmsh.model.geo.addPoint(-6, 10 - delta, 0, delta, 6)
gmsh.model.geo.addPoint(-6, 10 + delta, 0, delta, 7)
gmsh.model.geo.addPoint(-6 + 0.866 * delta, 10 + 0.5 * delta, 0, delta, 8)
gmsh.model.geo.addPoint(-6 - 0.866 * delta, 10 + 0.5 * delta, 0, delta, 9)
gmsh.model.geo.addPoint(-6 + 0.866 * delta, 10 - 0.5 * delta, 0, delta, 10)
gmsh.model.geo.addPoint(-6 - 0.866 * delta, 10 - 0.5 * delta, 0, delta, 11)

gmsh.model.geo.addLine(7, 8, 5)
gmsh.model.geo.addLine(8, 10, 6)
gmsh.model.geo.addLine(10, 6, 7)
gmsh.model.geo.addLine(6, 11, 8)
gmsh.model.geo.addLine(11, 9, 9)
gmsh.model.geo.addLine(9, 7, 10)

gmsh.model.geo.addCurveLoop([5, 6, 7, 8, 9, 10], 2)
gmsh.model.geo.addPlaneSurface([2], 2)

# BHE surfaces 2
gmsh.model.geo.addPoint(6, 10, 0, delta, 12)
gmsh.model.geo.addPoint(6, 10 - delta, 0, delta, 13)
gmsh.model.geo.addPoint(6, 10 + delta, 0, delta, 14)
gmsh.model.geo.addPoint(6 + 0.866 * delta, 10 + 0.5 * delta, 0, delta, 15)
gmsh.model.geo.addPoint(6 - 0.866 * delta, 10 + 0.5 * delta, 0, delta, 16)
gmsh.model.geo.addPoint(6 + 0.866 * delta, 10 - 0.5 * delta, 0, delta, 17)
gmsh.model.geo.addPoint(6 - 0.866 * delta, 10 - 0.5 * delta, 0, delta, 18)

gmsh.model.geo.addLine(14, 15, 11)
gmsh.model.geo.addLine(15, 17, 12)
gmsh.model.geo.addLine(17, 13, 13)
gmsh.model.geo.addLine(13, 18, 14)
gmsh.model.geo.addLine(18, 16, 15)
gmsh.model.geo.addLine(16, 14, 16)

gmsh.model.geo.addCurveLoop([11, 12, 13, 14, 15, 16], 3)
gmsh.model.geo.addPlaneSurface([3], 3)

# BHE surfaces 3
gmsh.model.geo.addPoint(0, 10, 0, delta, 19)
gmsh.model.geo.addPoint(0, 10 - delta, 0, delta, 20)
gmsh.model.geo.addPoint(0, 10 + delta, 0, delta, 21)
gmsh.model.geo.addPoint(0 + 0.866 * delta, 10 + 0.5 * delta, 0, delta, 22)
gmsh.model.geo.addPoint(0 - 0.866 * delta, 10 + 0.5 * delta, 0, delta, 23)
gmsh.model.geo.addPoint(0 + 0.866 * delta, 10 - 0.5 * delta, 0, delta, 24)
gmsh.model.geo.addPoint(0 - 0.866 * delta, 10 - 0.5 * delta, 0, delta, 25)

gmsh.model.geo.addLine(21, 22, 17)
gmsh.model.geo.addLine(22, 24, 18)
gmsh.model.geo.addLine(24, 20, 19)
gmsh.model.geo.addLine(20, 25, 20)
gmsh.model.geo.addLine(25, 23, 21)
gmsh.model.geo.addLine(23, 21, 22)

gmsh.model.geo.addCurveLoop([17, 18, 19, 20, 21, 22], 4)
gmsh.model.geo.addPlaneSurface([4], 4)
gmsh.model.geo.synchronize()

The `gmsh.model.geo.extrude` command extrudes BHE surface 1, 2 and 3 along the z axis and automatically creates a new volume (as well as all the needed points, curves and surfaces).
The function takes a vector of (dim, tag) pairs as input as well as the translation vector, and returns a vector of (dim, tag) pairs as output.
For the BHE 1 and 2 in translational vector, x-coordinate is set to 2 and -2 respectively in order to create inclined BHE along x-direction.
As a result, the end point of BHEs will be deflected by 2 units along (+) and (-) x-direction.

The 2D mesh extrusion is done with the same `extrude()` function, but by specifying element 'Layers' (Here, one layer each with 10 subdivisions).
The number of elements for each layer and the (end) height of each layer are specified in two vectors.
The last (optional) argument for the extrude() function specifies whether the extruded mesh should be recombined or not.
In this case, it is `True` since we want to recombine and produce prism mesh elements.

Later, BHE points 5, 12 and 19 have been extruded in the same way to create line elements (`Lr`, `Ll` and `Lm`) which represent BHEs.

In [8]:
P = gmsh.model.geo.extrude([(2, 2)], 2, 0, -10, [10], [1], True)  # BHE surface 1
Q = gmsh.model.geo.extrude([(2, 3)], -2, 0, -10, [10], [1], True)  # BHE surface 2
R = gmsh.model.geo.extrude([(2, 4)], 0, 0, -10, [10], [1], True)  # BHE surface 3

Lr = gmsh.model.geo.extrude([(0, 5)], 2, 0, -10, [10], [1], True)  # BHE 1
Ll = gmsh.model.geo.extrude([(0, 12)], -2, 0, -10, [10], [1], True)  # BHE 2
Lm = gmsh.model.geo.extrude([(0, 19)], 0, 0, -10, [10], [1], True)  # BHE 3

gmsh.model.geo.synchronize()

Finally, geometry surface 1 is created by combining curve loop 1, 2, 3 and 4.
Here, 2, 3, 4 are BHE curve loops and 1 is geometry curve loop.
After that, 6 surfaces of geometry and 21 surfaces from 3 BHE hexagonal objects are combined to create a surface loop.
Later, volume is added to the surface loop using API function `gmsh.model.geo.addVolume`.
Before creating mesh, `gmsh.model.geo.synchronize` is used to synchronize the CAD entities with the Gmsh model, which will create the relevant Gmsh data structures.

In [9]:
gmsh.model.geo.addPlaneSurface([1, 2, 3, 4], 1)

sl = gmsh.model.geo.addSurfaceLoop(
    [
        1,
        5,
        6,
        7,
        8,
        9,
        204,
        183,
        187,
        191,
        195,
        199,
        203,
        140,
        119,
        123,
        127,
        131,
        135,
        139,
        172,
        151,
        155,
        159,
        163,
        167,
        171,
    ]
)
v = gmsh.model.geo.addVolume([sl])

gmsh.model.geo.synchronize()

Later `gmsh.model.addPhysicalGroup` command used to group elementary geometrical entities to define material properties.
Gmsh will export in output files only mesh elements that belong to at least one physical group.
Physical groups are also identified by tags, i.e. strictly positive integers, that should be unique per dimension (0D, 1D, 2D or 3D).
Here, BHE 1, 2 and 3 are tagged by 2, 3, 4 physical group respectively.

In [10]:
gmsh.model.addPhysicalGroup(3, [P[1][1], Q[1][1], R[1][1], v], 1)
gmsh.model.addPhysicalGroup(1, [Lr[1][1]], 2)
gmsh.model.addPhysicalGroup(1, [Ll[1][1]], 3)
gmsh.model.addPhysicalGroup(1, [Lm[1][1]], 4)

4

Meshes generated with Gmsh must be converted to VTU file format later. Currently, the only supported Gmsh format is 2.2

In [11]:
gmsh.option.setNumber("Mesh.MshFileVersion", 2.2)

Then We can then generate a 3D mesh and save it to disk

In [12]:
gmsh.model.mesh.generate(3)

gmsh.model.mesh.removeDuplicateNodes()

gmsh.write(f"{out_dir}/{bhe_mesh_file_name}.msh")

Info    : Meshing 1D...
Info    : [  0%] Meshing curve 1 (Line)
Info    : [ 10%] Meshing curve 2 (Line)
Info    : [ 10%] Meshing curve 3 (Line)
Info    : [ 10%] Meshing curve 4 (Line)
Info    : [ 10%] Meshing curve 5 (Line)
Info    : [ 10%] Meshing curve 6 (Line)
Info    : [ 10%] Meshing curve 7 (Line)
Info    : [ 20%] Meshing curve 8 (Line)
Info    : [ 20%] Meshing curve 9 (Line)
Info    : [ 20%] Meshing curve 10 (Line)
Info    : [ 20%] Meshing curve 11 (Line)
Info    : [ 20%] Meshing curve 12 (Line)
Info    : [ 20%] Meshing curve 13 (Line)
Info    : [ 20%] Meshing curve 14 (Line)
Info    : [ 30%] Meshing curve 15 (Line)
Info    : [ 30%] Meshing curve 16 (Line)
Info    : [ 30%] Meshing curve 17 (Line)
Info    : [ 30%] Meshing curve 18 (Line)
Info    : [ 30%] Meshing curve 19 (Line)
Info    : [ 30%] Meshing curve 20 (Line)
Info    : [ 30%] Meshing curve 21 (Line)
Info    : [ 40%] Meshing curve 22 (Line)
Info    : [ 40%] Meshing curve 101 (Line)
Info    : [ 40%] Meshing curve 102 (Line)

Info    : Done tetrahedrizing 8837 nodes (Wall 0.0750235s, CPU 0.071299s)
Info    : Reconstructing mesh...
Info    :  - Creating surface mesh
Info    :  - Identifying boundary edges
Info    :  - Recovering boundary
Info    : Done reconstructing mesh (Wall 0.198039s, CPU 0.181153s)
Info    : Found volume 4


Info    : It. 0 - 0 nodes created - worst tet radius 11.0009 (nodes removed 0 0)
Info    : It. 500 - 500 nodes created - worst tet radius 3.32294 (nodes removed 0 0)
Info    : It. 1000 - 1000 nodes created - worst tet radius 2.71805 (nodes removed 0 0)
Info    : It. 1500 - 1500 nodes created - worst tet radius 2.42141 (nodes removed 0 0)
Info    : It. 2000 - 1998 nodes created - worst tet radius 2.22495 (nodes removed 0 2)
Info    : It. 2500 - 2498 nodes created - worst tet radius 2.07679 (nodes removed 0 2)
Info    : It. 3000 - 2995 nodes created - worst tet radius 1.97088 (nodes removed 0 5)
Info    : It. 3500 - 3491 nodes created - worst tet radius 1.87597 (nodes removed 0 9)
Info    : It. 4000 - 3982 nodes created - worst tet radius 1.80491 (nodes removed 0 18)


Info    : It. 4500 - 4461 nodes created - worst tet radius 1.74426 (nodes removed 0 39)
Info    : It. 5000 - 4929 nodes created - worst tet radius 1.69201 (nodes removed 1 70)
Info    : It. 5500 - 5391 nodes created - worst tet radius 1.64551 (nodes removed 1 108)
Info    : It. 6000 - 5852 nodes created - worst tet radius 1.60605 (nodes removed 2 146)
Info    : It. 6500 - 6267 nodes created - worst tet radius 1.57436 (nodes removed 11 222)
Info    : It. 7000 - 6683 nodes created - worst tet radius 1.54205 (nodes removed 17 300)
Info    : It. 7500 - 7131 nodes created - worst tet radius 1.5109 (nodes removed 18 351)
Info    : It. 8000 - 7582 nodes created - worst tet radius 1.48016 (nodes removed 20 398)
Info    : It. 8500 - 8039 nodes created - worst tet radius 1.45303 (nodes removed 20 441)
Info    : It. 9000 - 8526 nodes created - worst tet radius 1.42546 (nodes removed 25 449)
Info    : It. 9500 - 9020 nodes created - worst tet radius 1.39807 (nodes removed 26 454)
Info    : It. 100

Info    : It. 11500 - 10971 nodes created - worst tet radius 1.31699 (nodes removed 32 497)
Info    : It. 12000 - 11450 nodes created - worst tet radius 1.29948 (nodes removed 32 518)
Info    : It. 12500 - 11947 nodes created - worst tet radius 1.28227 (nodes removed 34 519)
Info    : It. 13000 - 12441 nodes created - worst tet radius 1.26672 (nodes removed 36 523)
Info    : It. 13500 - 12915 nodes created - worst tet radius 1.59762 (nodes removed 38 547)
Info    : It. 14000 - 13390 nodes created - worst tet radius 1.23693 (nodes removed 42 568)
Info    : It. 14500 - 13867 nodes created - worst tet radius 1.22324 (nodes removed 42 591)
Info    : It. 15000 - 14338 nodes created - worst tet radius 1.20993 (nodes removed 44 618)
Info    : It. 15500 - 14822 nodes created - worst tet radius 1.19817 (nodes removed 44 634)
Info    : It. 16000 - 15307 nodes created - worst tet radius 1.18664 (nodes removed 47 646)
Info    : It. 16500 - 15803 nodes created - worst tet radius 1.17376 (nodes remo

...

Info    : Done optimizing pyramids for hybrid mesh


Info    : Done meshing 3D (Wall 2.24816s, CPU 2.2224s)
Info    : Optimizing mesh...
Info    : Optimizing volume 4


Info    : Optimization starts (volume = 4779.33) with worst = 2.81445e-06 / average = 0.776624:
Info    : 0.00 < quality < 0.10 :       583 elements
Info    : 0.10 < quality < 0.20 :      1302 elements
Info    : 0.20 < quality < 0.30 :      2301 elements
Info    : 0.30 < quality < 0.40 :      3747 elements
Info    : 0.40 < quality < 0.50 :      5692 elements
Info    : 0.50 < quality < 0.60 :      9511 elements
Info    : 0.60 < quality < 0.70 :     19406 elements
Info    : 0.70 < quality < 0.80 :     43088 elements
Info    : 0.80 < quality < 0.90 :     71643 elements
Info    : 0.90 < quality < 1.00 :     37056 elements
Info    : 3980 edge swaps, 0 node relocations (volume = 4779.33): worst = 2.81445e-06 / average = 0.78917 (Wall 0.0950505s, CPU 0.094915s)
Info    : 4065 edge swaps, 0 node relocations (volume = 4779.33): worst = 2.81445e-06 / average = 0.789322 (Wall 0.118432s, CPU 0.118323s)
Info    : 0.00 < quality < 0.10 :        42 elements
Info    : 0.10 < quality < 0.20 :        26

Info    : Found 33 duplicate nodes 
Info    : Removed 33 duplicate mesh nodes
Info    : Done removing duplicate mesh nodes
Info    : Writing '/var/lib/gitlab-runner/builds/vZ6vnZiU/0/ogs/build/release-all/web/content/docs/tutorials/Inclined_bhe_meshing/notebook-inclined_bhe_meshing/inclined_bhe_mesh_file.msh'...


Info    : Done writing '/var/lib/gitlab-runner/builds/vZ6vnZiU/0/ogs/build/release-all/web/content/docs/tutorials/Inclined_bhe_meshing/notebook-inclined_bhe_meshing/inclined_bhe_mesh_file.msh'


Launch the GUI to see the results. Later `gmsh.finalize()` will be called when done using Gmsh Python API

In [13]:
if "CI" not in os.environ:
    gmsh.fltk.run()

gmsh.finalize()

If everything runs well, you will see the following mesh with incline BHEs.

![inclined3DBHE.png](./inclined3DBHE.png)

2D version will look like this.
![inclined2DBHE.png](./inclined2DBHE.png)

Now checking whether the Gmsh format mesh file is properly created. If not give an error message.

In [14]:
check_file = Path(f"{out_dir}/{bhe_mesh_file_name}.msh").is_file()
if check_file:
    print("Creation of BHE mesh in Gmsh format was successful.")
else:
    print("Error! Gmsh file is not properly created in the BHE meshing tutorial.")
    raise SystemExit()

Creation of BHE mesh in Gmsh format was successful.


Finally, the mesh file which has been created using the python interface of Gmsh, will be converted to OGS mesh, in particular to VTU file format. Please, add ogs.exe to the directory of this example file to run GMSH2OGS or give the full path of your ogs executable. Here, option -v (--validation) validate the mesh and shows crucial information of mesh. Option -i takes Gmsh input file name as string and -o is output file name as string as well.

In [15]:
!GMSH2OGS -i {out_dir}/{bhe_mesh_file_name}.msh -o {out_dir}/{bhe_mesh_file_name}.vtu -v

info: Reading /var/lib/gitlab-runner/builds/vZ6vnZiU/0/ogs/build/release-all/web/content/docs/tutorials/Inclined_bhe_meshing/notebook-inclined_bhe_meshing/inclined_bhe_mesh_file.msh.


info: 	... finished.
info: Nr. Nodes: 34959.
info: Nr. Elements: 191269.
info: Mem for mesh: 38 MiB
info: Time for reading: 1.497844 seconds.
info: Read 34959 nodes and 191269 elements.
info: Please check your mesh carefully!
info: Degenerated or redundant mesh elements can cause OGS to stop or misbehave.
info: Use the -e option to delete redundant line elements.
info: Axis aligned bounding box: 	x [-10, 10) (extent 20)
	y [0, 20) (extent 20)
	z [-12, 4.94066e-324) (extent 12)


info: Edge length: [0.139918, 1.3739]
info: Number of elements in the mesh:
info: 	Lines: 30
info: 	Tetrahedrons: 190879
info: 	Pyramids: 180
info: 	Prisms: 180
info: There are 1 properties in the mesh:
info: 	MaterialIDs: (191269 values) [0, 3]
info: Mesh Quality Control:
info: Looking for unused nodes...
info: Found 0 potentially collapsible nodes.
info: Testing mesh element geometry:


info: No errors found.
info: No elements found with zero volume.

info: No elements found with non coplanar nodes.

info: No elements found with non-convex geometry.

info: No elements found with wrong node order.

info: 1 property vectors copied, 0 vectors skipped.
info: 3 hole(s) detected within the mesh


The above conversion tool also shows that there exist line, tetrahedrons, pyramids and prism elements.The number of lines, tetrahedrons, pyramids  and prism element is respectively 30, 190918, 180 and 180 with no error.

In [16]:
check_file = Path(f"{out_dir}/{bhe_mesh_file_name}.vtu").is_file()
if check_file:
    print("Conversion of mesh file from Gmsh to VTU format was successful.")
else:
    print(
        "Error! Gmsh file is not properly converted to VTU format in the BHE meshing tutorial."
    )
    raise SystemExit()

Conversion of mesh file from Gmsh to VTU format was successful.
